In [ ]:
import random, os

In [ ]:
start = [random.randint(1,99) for x in range(150)]

In [ ]:
start.sort()

In [ ]:
print(start)

In [ ]:
end = [start[x]+random.randint(10,51) for x in range(150)]

In [ ]:
print(end)

In [ ]:
chr = [1 for x in range(150)]

In [ ]:
print(chr)

In [ ]:
with open("test.bed","w") as f: 
    for x in range(150): 
        f.write("%s\t%s\t%s\n" % (chr[x], start[x], end[x]))

In [ ]:
import glob

In [ ]:
glob.glob("*")

In [ ]:
############# Exercice 1 ###########################

In [ ]:
f = open("test.bed","r")

In [ ]:
bed = list()

In [ ]:
for l in f: 
    bed.append(l.rstrip('\n').split('\t'))

In [ ]:
def load_table(f,d):
    out = []
    with open(f,"r") as ff:
        for l in ff:
            out.append(l.rstrip('\n').split(d))
    return out

In [ ]:
print(load_table("test.bed",'\t'))

In [ ]:
print(bed)

In [ ]:
import csv

In [ ]:
bed_csv = list()
with open("test.bed", "r") as ff:
    reader = csv.reader(ff,delimiter='\t')
    for line in reader:
        bed_csv.append(line)

In [ ]:
print(bed_csv)

In [ ]:
for line in bed:
    line[0] = 'chr'+line[0]

In [ ]:
print(bed)

In [ ]:
#[i for i in bed if int(i[2])-int(i[1])>50]
for i in bed:
    if int(i[2])-int(i[1])>50:
        print(i)

In [ ]:
def longer(f,l):
    out = []
    for i in f:
        if int(i[2])-int(i[1])>l:
            out.append(i)
    return out

In [ ]:
print(longer(bed,50))

In [ ]:
############# Exercice 2 ###########################

In [ ]:
wig = dict()

In [ ]:
for line in bed:
    for bp in range(int(line[1]),int(line[2])+1):
        if bp in wig:
            wig[bp] = wig[bp]+1
        else:
            wig[bp] = 1

In [ ]:
print(wig)

In [ ]:
with open("test.wig","w") as f:
    f.write("variableStep chrom=%s\n" % bed[0][0])
    for i,x in wig.items():
        f.write("%s\t%s\n" % (i,x))

In [ ]:
############# Exercice 3 ###########################

In [ ]:
sam = load_table("test.sam","\t")

In [ ]:
print(sam[0])

In [ ]:
mapped = []
for l in sam:
    if int(l[1]) & 4 == 0:
        mapped.append(l)

In [ ]:
len(sam)

In [ ]:
len(mapped)

In [ ]:
len([l for l in sam if int(l[1]) & 2 != 0])

In [ ]:
def bitflag(table,flags):
    out = []
    for l in table:
        ok = True
        for c in flags:
            if int(l[1]) & c == 0:
                ok = False
                break
        if ok:
            out.append(l)
    return out

In [ ]:
len(bitflag(sam,[]))

In [ ]:
############# Homework ###########################

In [ ]:
fd = open("test.fastq","r")

In [ ]:
i = 0
fastq = []
line = []

# read the input file and store it as a list of 4 columns (0: header, 1: sequence, 2: '+', 3: qual. sequence)
for l in fd:
    line.append(l.rstrip('\n\r'))
    if i%4 == 3:
        fastq.append(line)
        line=[]
    i = i+1
    

In [ ]:
len(fastq)

In [ ]:
def cut_sequence(sq, min_mean = 30, ws = 10):
    # sq : quality sequence
    # ws = 10 : window size
    # min_mean = 30 # mean quality threshold
    w = 0
    while w <= len(sq)-ws:
        # read part of qual. sequence (window sequence)
        window = sq[w:w+ws] 
        
        # get mean quality of window sequence
        for c in window: # compute per-base quality and summarise
            sum = sum + ord(c)-33
        mean = sum/ws
        
        # if mean quality is not enough, break the loop and return end position of window
        if(mean >= min_mean): 
            #print(w, window)
            #print(mean)
            w = w+1
        else:
            w = w
            break
    return w+ws

In [ ]:
out = []
for l in fastq:
    window_size = 10 # define window size
    min_qual = 33 # define min mean quality
    
    # get end position of read satisfying quality check
    end = cut_sequence(l[3], min_qual, window_size)
    
    # check if quality is not sufficient in whole read
    if end > window_size:
        out.append(l)
        out[-1][1] = out[-1][1][:end]
        out[-1][3] = out[-1][3][:end]


In [ ]:
with open("test_trimmed.fastq","w") as f:
    for l in out:
        f.write(l[0]+'\n')
        f.write(l[1]+'\n')
        f.write(l[2]+'\n')
        f.write(l[3]+'\n')